In [1]:
%%capture

import pandas as pd
import geopandas as gpd
from calitp_data_analysis.sql import query_sql
from calitp_data_analysis.gcs_geopandas import GCSGeoPandas
from calitp_data_analysis.geography_utils import CA_NAD83Albers_m, WGS84
import calitp_data_analysis.magics
gcsgp = GCSGeoPandas()
from shared_utils import gtfs_utils_v2, rt_utils

import utils
import update_vars
import altair as alt
import numpy as np
import shapely
import branca

import importlib
importlib.reload(utils)
importlib.reload(update_vars)

In [2]:
import chart_utils

# Passenger Flow and Ridership Charts by Route and Origin/Destination

* Hues represent origin stops (and may repeat where there are many)
* Within each origin group, darker shades represent longer O/D pairs
* Currently based on April 2025 figures only

In [3]:
analysis_date = update_vars.ANALYSIS_DATE

In [4]:
feeds = gtfs_utils_v2.schedule_daily_feed_to_gtfs_dataset_name(analysis_date)

In [5]:
sanj = feeds.query('name == "Amtrak San Joaquins Schedule"')

In [6]:
sanj_shapes = gtfs_utils_v2.get_shapes(analysis_date, operator_feeds=sanj.feed_key, shape_cols=update_vars.shape_cols)
sanj_shapes = sanj_shapes.to_crs(CA_NAD83Albers_m)
sanj_shapes = sanj_shapes.assign(length_meters = sanj_shapes.geometry.length)

/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'GEOGRAPHY' of column 'pt_array'
  sqlalchemy.util.warn(


In [7]:
sanj_trips = gtfs_utils_v2.get_trips(analysis_date, operator_feeds=sanj.feed_key, trip_cols=update_vars.trip_cols).query('route_type == "3"')

In [8]:
sanj_stops = gtfs_utils_v2.get_stops(analysis_date, operator_feeds=sanj.feed_key, stop_cols=update_vars.stop_cols).to_crs(CA_NAD83Albers_m)

/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'GEOGRAPHY' of column 'pt_geom'
  sqlalchemy.util.warn(


In [9]:
sanj_st = gtfs_utils_v2.get_stop_times(analysis_date, operator_feeds=sanj.feed_key, get_df=True,
                                      trip_df = sanj_trips, stop_time_cols=update_vars.stop_time_cols)

/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'arrival_time_interval'
  sqlalchemy.util.warn(
/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'departure_time_interval'
  sqlalchemy.util.warn(
/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'start_pickup_drop_off_window_interval'
  sqlalchemy.util.warn(
/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'end_pickup_drop_off_window_interval'
  sqlalchemy.util.warn(


In [10]:
bus_st = sanj_st.merge(sanj_trips[['trip_id', 'direction_id', 'route_id', 'route_short_name',
                                   'shape_array_key', 'shape_id']], on='trip_id')

In [11]:
sanj_shapes_trip_info = (sanj_shapes.merge(sanj_trips.drop_duplicates(subset=['shape_array_key']), on = ['shape_array_key', 'feed_key'])
                            .drop(columns=['base64_url', 'regional_feed_type', 'block_id',
                                           'route_desc', 'agency_id', 'network_id',
                                          'route_key'])
                        )

In [12]:
gcsgp.geo_data_frame_to_parquet(sanj_shapes_trip_info, f'{update_vars.GCS_PATH}intermediate/sanj_shapes_trip_info_{analysis_date}.parquet')

In [13]:
sanj_long_shapes = utils.longest_by_route_dir(sanj_shapes_trip_info)

In [15]:
#  charts only show one month for now
source_ridership = utils.read_format_ridership().query('trip_year == 2025 & trip_month == 4')

In [16]:
bus_stops = sanj_st.stop_id.unique()

In [17]:
get_ridership_unique_stops = lambda df: np.union1d(df.orig, df.dest)

In [18]:
rider_stops = get_ridership_unique_stops(source_ridership)

In [19]:
sanj_bus_to_rider_stops = dict(zip(bus_stops, [x[1:] for x in bus_stops]))
sanj_bus_to_rider_stops['bLOS'] = 'LAX'

In [20]:
bus_st = pd.merge(sanj_stops[['stop_id', 'geometry']], bus_st, on='stop_id')
bus_st = bus_st.assign(amtrak_stop = bus_st.stop_id.map(sanj_bus_to_rider_stops)).sort_values(['trip_id', 'stop_sequence'])

In [21]:
# pd.Series(sanj_bus_to_rider_stops.values()).isin(pd.Series(rider_stops)).value_counts()

# gtfs_no_rider_data = pd.Series(sanj_bus_to_rider_stops.values())[~pd.Series(sanj_bus_to_rider_stops.values()).isin(pd.Series(rider_stops))]
# gtfs_no_rider_data #  OK -- all either served by RABA/YARTS or outside CA...

## Route 1

In [22]:
rt1_test = sanj_long_shapes.query('route_id == "1"')

In [23]:
rt1_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
0  Amtrak San Joaquins Schedule          Route 1   
1  Amtrak San Joaquins Schedule          Route 1   

                                     route_long_name shape_id  
0  Fresno/Bekersfield - Los Angeles- SantaAna - O...     jfy7  
1  Fresno/Bekersfield - Los Angeles- SantaAna - O...     xurp

### By Distance Traveled

In [171]:
chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A')

alt.Chart(...)

### By Travel Time

In [172]:
chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A', how='time')

alt.Chart(...)

## Route 1 - other direction

### By Distance Traveled

In [26]:
chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A')

### By Travel Time

In [26]:
chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A', how='time')

## Route 1b

In [28]:
rt1b_test = sanj_long_shapes.query('route_id == "1"')

In [29]:
rt1b_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
0  Amtrak San Joaquins Schedule          Route 1   
1  Amtrak San Joaquins Schedule          Route 1   

                                     route_long_name shape_id  
0  Fresno/Bekersfield - Los Angeles- SantaAna - O...     jfy7  
1  Fresno/Bekersfield - Los Angeles- SantaAna - O...     xurp

### By Distance Traveled

In [30]:
chart_utils.flow_chart_from_shape_trip_row(rt1b_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1B')

### By Travel Time

In [ ]:
chart_utils.flow_chart_from_shape_trip_row(rt1b_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1B', how='time')

## Route 1b - other direction

### By Distance Traveled

In [32]:
chart_utils.flow_chart_from_shape_trip_row(rt1b_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1B')

### By Travel Time

In [32]:
chart_utils.flow_chart_from_shape_trip_row(rt1b_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1B', how='time')

## Route 1C

In [34]:
rt1c_test = sanj_long_shapes.query('route_id == "1c"')

In [35]:
rt1c_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
14  Amtrak San Joaquins Schedule         Route 1c   
15  Amtrak San Joaquins Schedule         Route 1c   

                            route_long_name shape_id  
14  Bakersfield to Los Angeles/Santa Monica     wo7l  
15  Bakersfield to Los Angeles/Santa Monica     r66l

### By Distance Traveled

In [36]:
chart_utils.flow_chart_from_shape_trip_row(rt1c_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1C')

correcting LAX to SMN for Route 1c


### By Travel Time

In [36]:
chart_utils.flow_chart_from_shape_trip_row(rt1c_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1C', how='time')

correcting LAX to SMN for Route 1c


## Route 1C - other direction

### By Distance Traveled

In [38]:
chart_utils.flow_chart_from_shape_trip_row(rt1c_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1C')

correcting LAX to SMN for Route 1c


### By Travel Time

In [38]:
chart_utils.flow_chart_from_shape_trip_row(rt1c_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1C', how='time')

correcting LAX to SMN for Route 1c


## Route 3

* Operated by RABA Chico - Redding, seems to create a data gap in that section

### By Distance Traveled

In [40]:
rt3_test = sanj_long_shapes.query('route_id == "3"')

In [41]:
rt3_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
20  Amtrak San Joaquins Schedule          Route 3   
21  Amtrak San Joaquins Schedule          Route 3   

                route_long_name shape_id  
20  Redding Sacramento Stockton     1wk1  
21  Redding Sacramento Stockton     1vos

In [42]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt3_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              # ridership_data_route='Rt 03'
                                                  )

### By Travel Time

In [43]:
chart

stop_id                        geometry                          feed_key  \
515    bSKN   POINT (-112764.152 -7163.317)  d9e1e77d0754b712fc608741ae3836f5   
337    bEKG   POINT (-129095.785 46467.612)  d9e1e77d0754b712fc608741ae3836f5   
581    bSAC   POINT (-130615.865 63942.803)  d9e1e77d0754b712fc608741ae3836f5   
143    bSCS   POINT (-130080.095 63332.562)  d9e1e77d0754b712fc608741ae3836f5   
262    bMRV  POINT (-137926.355 126473.810)  d9e1e77d0754b712fc608741ae3836f5   
256    bORV  POINT (-135061.385 168250.375)  d9e1e77d0754b712fc608741ae3836f5   
226    bCIC  POINT (-158133.673 191273.497)  d9e1e77d0754b712fc608741ae3836f5   
148    bRBF  POINT (-190256.210 242524.873)  d9e1e77d0754b712fc608741ae3836f5   
156    bRDD  POINT (-202574.887 287818.356)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
515    3715              0     16:45:00       16:45:00        60300   
337    3715              1     17:35:00       17:35:00        63300   
581    3715              2     17:50:00       17:50:00        64200   
143    3715              3     18:15:00       18:15:00        65700   
262    3715              4     19:05:00       19:05:00        68700   
256    3715              5     19:40:00       19:40:00        70800   
226    3715              6     20:10:00       20:10:00        72600   
148    3715              7     21:05:00       21:05:00        75900   
156    3715              8     21:35:00       21:35:00        77700   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
515          60300            16  ...             0         3   
337          63300            17  ...             0         3   
581          64200            17  ...             0         3   
143          65700            18  ...             0         3   
262          68700            19  ...             0         3   
256          70800            19  ...             0         3   
226          72600            20  ...             0         3   
148          75900            21  ...             0         3   
156          77700            21  ...             0         3   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
515          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         SKN   
337          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         EKG   
581          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         SAC   
143          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         SCS   
262          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         MRV   
256          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         ORV   
226          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         CIC   
148          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         RBF   
156          Route 3  343e18a20cd18a4e3878e5eaf55cf0e1     1wk1         RDD   

       stop_meters  stop_miles  next_miles  \
515       0.000000           0        38.0   
337   60761.288552          38        50.0   
581   80415.495720          50        50.0   
143   81227.557141          50        92.0   
262  148199.071623          92       120.0   
256  192477.529596         120       142.0   
226  228081.793782         142       185.0   
148  297382.543668         185       217.0   
156  348575.130793         217         NaN   

                                            mile_range  
515  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
337  [38.0, 39.0, 40.0, 41.0, 42.0, 43.0, 44.0, 45....  
581                                                 []  
143  [50.0, 51.0, 52.0, 53.0, 54.0, 55.0, 56.0, 57....  
262  [92.0, 93.0, 94.0, 95.0, 96.0, 97.0, 98.0, 99....  
256  [120.0, 121.0, 122.0, 123.0, 124.0, 125.0, 126...  
226  [142.0, 143.0, 144.0, 145.0, 146.0, 147.0, 148...  
148  [185.0, 186.0, 187.0, 188.0, 189.0, 190.0, 191...  
156                                               None  

[9 rows 

## Route 3 - other direction

* Operated by RABA Chico - Redding, seems to create a data gap in that section

In [44]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt3_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              # ridership_data_route='Rt 03'
                                                  )

In [45]:
chart

stop_id                        geometry                          feed_key  \
154    bRDD  POINT (-202574.887 287818.356)  d9e1e77d0754b712fc608741ae3836f5   
146    bRBF  POINT (-190256.210 242524.873)  d9e1e77d0754b712fc608741ae3836f5   
223    bCIC  POINT (-158133.673 191273.497)  d9e1e77d0754b712fc608741ae3836f5   
253    bORV  POINT (-135061.385 168250.375)  d9e1e77d0754b712fc608741ae3836f5   
259    bMRV  POINT (-137926.355 126473.810)  d9e1e77d0754b712fc608741ae3836f5   
570    bSAC   POINT (-130615.865 63942.803)  d9e1e77d0754b712fc608741ae3836f5   
333    bEKG   POINT (-129095.785 46467.612)  d9e1e77d0754b712fc608741ae3836f5   
505    bSKN   POINT (-112764.152 -7163.317)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
154    3712              0      6:05:00        6:05:00        21900   
146    3712              1      6:40:00        6:40:00        24000   
223    3712              2      7:45:00        7:45:00        27900   
253    3712              3      8:10:00        8:10:00        29400   
259    3712              4      8:45:00        8:45:00        31500   
570    3712              5      9:50:00        9:50:00        35400   
333    3712              6     10:20:00       10:20:00        37200   
505    3712              7     11:05:00       11:05:00        39900   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
154          21900             6  ...             1         3   
146          24000             6  ...             1         3   
223          27900             7  ...             1         3   
253          29400             8  ...             1         3   
259          31500             8  ...             1         3   
570          35400             9  ...             1         3   
333          37200            10  ...             1         3   
505          39900            11  ...             1         3   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
154          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         RDD   
146          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         RBF   
223          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         CIC   
253          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         ORV   
259          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         MRV   
570          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         SAC   
333          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         EKG   
505          Route 3  e6b4246a642170ee749bb4c1f7823464     1vos         SKN   

       stop_meters  stop_miles  next_miles  \
154       0.000000           0        32.0   
146   51071.280695          32        75.0   
223  120061.971486          75        97.0   
253  155595.645929          97       124.0   
259  199760.362842         124       165.0   
570  265967.359186         165       178.0   
333  287175.502660         178       216.0   
505  348080.301277         216         NaN   

                                            mile_range  
154  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
146  [32.0, 33.0, 34.0, 35.0, 36.0, 37.0, 38.0, 39....  
223  [75.0, 76.0, 77.0, 78.0, 79.0, 80.0, 81.0, 82....  
253  [97.0, 98.0, 99.0, 100.0, 101.0, 102.0, 103.0,...  
259  [124.0, 125.0, 126.0, 127.0, 128.0, 129.0, 130...  
570  [165.0, 166.0, 167.0, 168.0, 169.0, 170.0, 171...  
333  [178.0, 179.0, 180.0, 181.0, 182.0, 183.0, 184...  
505                                               None  

[8 rows x 21 columns]

## Route 6

In [46]:
rt6_test = sanj_long_shapes.query('route_id == "6"')

In [47]:
rt6_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name       route_long_name  \
22  Amtrak San Joaquins Schedule          Route 6  San Jose  - Stockton   
23  Amtrak San Joaquins Schedule          Route 6  San Jose  - Stockton   

   shape_id  
22     ywn1  
23     gwbp

In [48]:
import chart_utils
importlib.reload(chart_utils)

<module 'chart_utils' from '/home/jovyan/data-analyses/thruway_intercity_bus/chart_utils.py'>

In [49]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt6_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 06')

In [50]:
chart

stop_id                        geometry                          feed_key  \
390    bSJC  POINT (-168323.486 -74618.906)  d9e1e77d0754b712fc608741ae3836f5   
102    bFRT  POINT (-169727.006 -51332.322)  d9e1e77d0754b712fc608741ae3836f5   
94     bDBP  POINT (-167065.995 -33180.863)  d9e1e77d0754b712fc608741ae3836f5   
118    bLIV  POINT (-155592.104 -35397.770)  d9e1e77d0754b712fc608741ae3836f5   
182    bTRA  POINT (-126329.006 -27378.988)  d9e1e77d0754b712fc608741ae3836f5   
508    bSKN   POINT (-112764.152 -7163.317)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
390    3916              0     12:25:00       12:25:00        44700   
102    3916              1     12:50:00       12:50:00        46200   
94     3916              2     13:10:00       13:10:00        47400   
118    3916              3     13:25:00       13:25:00        48300   
182    3916              4     13:50:00       13:50:00        49800   
508    3916              5     15:05:00       15:05:00        54300   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
390          44700            12  ...             0         6   
102          46200            12  ...             0         6   
94           47400            13  ...             0         6   
118          48300            13  ...             0         6   
182          49800            13  ...             0         6   
508          54300            15  ...             0         6   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
390          Route 6  e693cab3aa5f7e380ea821f24bc0ad4a     ywn1         SJC   
102          Route 6  e693cab3aa5f7e380ea821f24bc0ad4a     ywn1         FRT   
94           Route 6  e693cab3aa5f7e380ea821f24bc0ad4a     ywn1         DBP   
118          Route 6  e693cab3aa5f7e380ea821f24bc0ad4a     ywn1         LIV   
182          Route 6  e693cab3aa5f7e380ea821f24bc0ad4a     ywn1         TRA   
508          Route 6  e693cab3aa5f7e380ea821f24bc0ad4a     ywn1         SKN   

       stop_meters  stop_miles  next_miles  \
390       0.000000           0        17.0   
102   27336.016775          17        33.0   
94    52645.297184          33        41.0   
118   66688.500646          41        62.0   
182   98977.158859          62        81.0   
508  130717.881493          81         NaN   

                                            mile_range  
390  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
102  [17.0, 18.0, 19.0, 20.0, 21.0, 22.0, 23.0, 24....  
94    [33.0, 34.0, 35.0, 36.0, 37.0, 38.0, 39.0, 40.0]  
118  [41.0, 42.0, 43.0, 44.0, 45.0, 46.0, 47.0, 48....  
182  [62.0, 63.0, 64.0, 65.0, 66.0, 67.0, 68.0, 69....  
508                                               None  

[6 rows x 21 columns]

In [51]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt6_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 06')

In [52]:
chart

stop_id                        geometry                          feed_key  \
501    bSKN   POINT (-112764.152 -7163.317)  d9e1e77d0754b712fc608741ae3836f5   
397    bSKT   POINT (-112209.777 -5834.688)  d9e1e77d0754b712fc608741ae3836f5   
181    bTRA  POINT (-126329.006 -27378.988)  d9e1e77d0754b712fc608741ae3836f5   
117    bLIV  POINT (-155592.104 -35397.770)  d9e1e77d0754b712fc608741ae3836f5   
93     bDBP  POINT (-167065.995 -33180.863)  d9e1e77d0754b712fc608741ae3836f5   
101    bFRT  POINT (-169727.006 -51332.322)  d9e1e77d0754b712fc608741ae3836f5   
387    bSJC  POINT (-168323.486 -74618.906)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
501    3911              0      8:45:00        8:45:00        31500   
397    3911              1      8:55:00        8:55:00        32100   
181    3911              2      9:05:00        9:05:00        32700   
117    3911              3      9:35:00        9:35:00        34500   
93     3911              4      9:45:00        9:45:00        35100   
101    3911              5     10:00:00       10:00:00        36000   
387    3911              6     10:35:00       10:35:00        38100   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
501          31500             8  ...             1         6   
397          32100             8  ...             1         6   
181          32700             9  ...             1         6   
117          34500             9  ...             1         6   
93           35100             9  ...             1         6   
101          36000            10  ...             1         6   
387          38100            10  ...             1         6   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
501          Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         SKN   
397          Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         SKT   
181          Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         TRA   
117          Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         LIV   
93           Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         DBP   
101          Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         FRT   
387          Route 6  8787f4ea5edc0980c3baec711c1fc2f3     gwbp         SJC   

       stop_meters  stop_miles  next_miles  \
501       0.000000           0         1.0   
397    1989.309648           1        22.0   
181   35764.321223          22        43.0   
117   68589.925965          43        51.0   
93    82331.291100          51        67.0   
101  107256.555425          67        83.0   
387  133292.196284          83         NaN   

                                            mile_range  
501                                              [0.0]  
397  [1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, ...  
181  [22.0, 23.0, 24.0, 25.0, 26.0, 27.0, 28.0, 29....  
117   [43.0, 44.0, 45.0, 46.0, 47.0, 48.0, 49.0, 50.0]  
93   [51.0, 52.0, 53.0, 54.0, 55.0, 56.0, 57.0, 58....  
101  [67.0, 68.0, 69.0, 70.0, 71.0, 72.0, 73.0, 74....  
387                                               None  

[7 rows x 21 columns]

## Route 7

In [53]:
rt7_test = sanj_long_shapes.query('route_id == "7"')

In [54]:
rt7_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
24  Amtrak San Joaquins Schedule          Route 7   
25  Amtrak San Joaquins Schedule          Route 7   

                    route_long_name shape_id  
24  Martinez-Napa-Santa Rosa-Arcata     h39u  
25  Martinez-Napa-Santa Rosa-Arcata     z99i

In [55]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt7_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 07')

In [56]:
chart

stop_id                        geometry                          feed_key  \
110    bHSU  POINT (-344088.518 324850.429)  d9e1e77d0754b712fc608741ae3836f5   
90     bARC  POINT (-344305.595 324335.903)  d9e1e77d0754b712fc608741ae3836f5   
98     bEKA  POINT (-351843.677 317115.025)  d9e1e77d0754b712fc608741ae3836f5   
106    bFTA  POINT (-350983.275 292942.169)  d9e1e77d0754b712fc608741ae3836f5   
206    bWTS  POINT (-288263.400 160269.582)  d9e1e77d0754b712fc608741ae3836f5   
174    bUKH  POINT (-276170.825 130953.104)  d9e1e77d0754b712fc608741ae3836f5   
35     bHEA   POINT (-249567.472 69416.776)  d9e1e77d0754b712fc608741ae3836f5   
325    bSRC   POINT (-237717.246 52250.917)  d9e1e77d0754b712fc608741ae3836f5   
209    bRPC   POINT (-236507.521 40169.960)  d9e1e77d0754b712fc608741ae3836f5   
129    bNAP   POINT (-199169.306 33655.150)  d9e1e77d0754b712fc608741ae3836f5   
341    bMTZ    POINT (-187507.730 2415.562)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
110    6318              0      9:40:00        9:40:00        34800   
90     6318              1      9:50:00        9:50:00        35400   
98     6318              2     10:10:00       10:10:00        36600   
106    6318              3     10:40:00       10:40:00        38400   
206    6318              4     12:45:00       12:45:00        45900   
174    6318              5     13:55:00       13:55:00        50100   
35     6318              6     14:40:00       14:40:00        52800   
325    6318              7     15:00:00       15:00:00        54000   
209    6318              8     15:15:00       15:15:00        54900   
129    6318              9     16:15:00       16:15:00        58500   
341    6318             10     17:30:00       17:30:00        63000   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
110          34800             9  ...             0         7   
90           35400             9  ...             0         7   
98           36600            10  ...             0         7   
106          38400            10  ...             0         7   
206          45900            12  ...             0         7   
174          50100            13  ...             0         7   
35           52800            14  ...             0         7   
325          54000            15  ...             0         7   
209          54900            15  ...             0         7   
129          58500            16  ...             0         7   
341          63000            17  ...             0         7   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
110          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         HSU   
90           Route 7  6cc81359f51dcf334db276fd672fc133     h39u         ARC   
98           Route 7  6cc81359f51dcf334db276fd672fc133     h39u         EKA   
106          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         FTA   
206          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         WTS   
174          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         UKH   
35           Route 7  6cc81359f51dcf334db276fd672fc133     h39u         HEA   
325          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         SRC   
209          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         RPC   
129          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         NAP   
341          Route 7  6cc81359f51dcf334db276fd672fc133     h39u         MTZ   

       stop_meters  stop_miles  next_miles  \
110       0.000000           0         1.0   
90     1344.873814           1         9.0   
98    14875.465755           9        29.0   
106   46100.506378          29       145.0   
206  232848.473039         145       168.0   
174  269726.335011         168       213.0   
35   343409.010921         213       227.0   
325  365178.283194         227       236.0   
209  379270.163698         236    

In [57]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt7_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 07'
                                                  )

In [58]:
chart

stop_id                        geometry                          feed_key  \
343    bMTZ    POINT (-187507.730 2415.562)  d9e1e77d0754b712fc608741ae3836f5   
319    bVAL   POINT (-197851.760 11657.868)  d9e1e77d0754b712fc608741ae3836f5   
130    bNAP   POINT (-199169.306 33655.150)  d9e1e77d0754b712fc608741ae3836f5   
312    bPTC   POINT (-230393.580 27675.140)  d9e1e77d0754b712fc608741ae3836f5   
211    bRPC   POINT (-236507.521 40169.960)  d9e1e77d0754b712fc608741ae3836f5   
327    bSRC   POINT (-237717.246 52250.917)  d9e1e77d0754b712fc608741ae3836f5   
36     bHEA   POINT (-249567.472 69416.776)  d9e1e77d0754b712fc608741ae3836f5   
175    bUKH  POINT (-276170.825 130953.104)  d9e1e77d0754b712fc608741ae3836f5   
207    bWTS  POINT (-288263.400 160269.582)  d9e1e77d0754b712fc608741ae3836f5   
107    bFTA  POINT (-350983.275 292942.169)  d9e1e77d0754b712fc608741ae3836f5   
99     bEKA  POINT (-351843.677 317115.025)  d9e1e77d0754b712fc608741ae3836f5   
91     bARC  POINT (-344305.595 324335.903)  d9e1e77d0754b712fc608741ae3836f5   
111    bHSU  POINT (-344088.518 324850.429)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
343    6311              0     10:15:00       10:15:00        36900   
319    6311              1     10:40:00       10:40:00        38400   
130    6311              2     11:10:00       11:10:00        40200   
312    6311              3     11:55:00       11:55:00        42900   
211    6311              4     12:15:00       12:15:00        44100   
327    6311              5     12:30:00       12:30:00        45000   
36     6311              6     12:50:00       12:50:00        46200   
175    6311              7     14:15:00       14:15:00        51300   
207    6311              8     14:45:00       14:45:00        53100   
107    6311              9     16:55:00       16:55:00        60900   
99     6311             10     17:20:00       17:20:00        62400   
91     6311             11     17:40:00       17:40:00        63600   
111    6311             12     17:50:00       17:50:00        64200   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
343          36900            10  ...             1         7   
319          38400            10  ...             1         7   
130          40200            11  ...             1         7   
312          42900            11  ...             1         7   
211          44100            12  ...             1         7   
327          45000            12  ...             1         7   
36           46200            12  ...             1         7   
175          51300            14  ...             1         7   
207          53100            14  ...             1         7   
107          60900            16  ...             1         7   
99           62400            17  ...             1         7   
91           63600            17  ...             1         7   
111          64200            17  ...             1         7   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
343          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         MTZ   
319          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         VAL   
130          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         NAP   
312          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         PTC   
211          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         RPC   
327          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         SRC   
36           Route 7  43317e820bab91e7eb3336e82444be1d     z99i         HEA   
175          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         UKH   
207          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         WTS   
107          Route 7  43317e820bab91e7eb3336e82444be1d     z99i         FTA   
99           Route 7  43317e820bab91e7eb3336e82444be1d     z99i         EKA   
91           Ro

## Route 10

* Seems to function as two halves with train connection in the middle, but a few passengers can and do ride through (for example Santa Barbara - Las Vegas)

In [59]:
rt10_test = sanj_long_shapes.query('route_id == "10"')

In [60]:
rt10_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name            route_long_name  \
2  Amtrak San Joaquins Schedule         Route 10  Santa Barbara - Las Vegas   
3  Amtrak San Joaquins Schedule         Route 10  Santa Barbara - Las Vegas   

  shape_id  
2     47nw  
3     j7gg

In [61]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt10_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 10'
                                                  )

In [62]:
chart

stop_id                        geometry                          feed_key  \
5      bSBU   POINT (13946.569 -400088.258)  d9e1e77d0754b712fc608741ae3836f5   
57     bSBA   POINT (28223.118 -400226.602)  d9e1e77d0754b712fc608741ae3836f5   
13     bCPN   POINT (43838.943 -402045.428)  d9e1e77d0754b712fc608741ae3836f5   
73     bVEC   POINT (64452.501 -415204.209)  d9e1e77d0754b712fc608741ae3836f5   
53     bOXN   POINT (75916.981 -423754.747)  d9e1e77d0754b712fc608741ae3836f5   
3      bSAP   POINT (85623.126 -407336.451)  d9e1e77d0754b712fc608741ae3836f5   
29     bFIL   POINT (99427.085 -401664.847)  d9e1e77d0754b712fc608741ae3836f5   
595    bBFD   POINT (89964.411 -293278.458)  d9e1e77d0754b712fc608741ae3836f5   
75     bTEH  POINT (140979.450 -319324.182)  d9e1e77d0754b712fc608741ae3836f5   
49     bMOJ  POINT (166476.324 -327734.430)  d9e1e77d0754b712fc608741ae3836f5   
15     bBAR  POINT (271678.696 -341476.512)  d9e1e77d0754b712fc608741ae3836f5   
17     bBBS  POINT (274084.197 -342886.533)  d9e1e77d0754b712fc608741ae3836f5   
47     bLVT  POINT (434891.255 -205377.488)  d9e1e77d0754b712fc608741ae3836f5   
39     bLAS  POINT (434817.143 -205406.193)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
5      5619              0     11:25:00       11:25:00        41100   
57     5619              1     11:55:00       11:55:00        42900   
13     5619              2     12:13:00       12:13:00        43980   
73     5619              3     12:34:00       12:34:00        45240   
53     5619              4     12:53:00       12:53:00        46380   
3      5619              5     13:19:00       13:19:00        47940   
29     5619              6     13:32:00       13:32:00        48720   
595    5619              7     16:05:00       16:05:00        57900   
75     5619              8     16:50:00       16:50:00        60600   
49     5619              9     17:14:00       17:14:00        62040   
15     5619             10     18:36:00       18:36:00        66960   
17     5619             11     19:05:00       19:05:00        68700   
47     5619             12     21:28:00       21:28:00        77280   
39     5619             13     21:45:00       21:45:00        78300   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
5            41100            11  ...             0        10   
57           42900            11  ...             0        10   
13           43980            12  ...             0        10   
73           45240            12  ...             0        10   
53           46380            12  ...             0        10   
3            47940            13  ...             0        10   
29           48720            13  ...             0        10   
595          57900            16  ...             0        10   
75           60600            16  ...             0        10   
49           62040            17  ...             0        10   
15           66960            18  ...             0        10   
17           68700            19  ...             0        10   
47           77280            21  ...             0        10   
39           78300            21  ...             0        10   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
5           Route 10  15e2f4643843159420d0e1b1563d7046     47nw         SBU   
57          Route 10  15e2f4643843159420d0e1b1563d7046     47nw         SBA   
13          Route 10  15e2f4643843159420d0e1b1563d7046     47nw         CPN   
73          Route 10  15e2f4643843159420d0e1b1563d7046     47nw         VEC   
53          Route 10  15e2f4643843159420d0e1b1563d7046     47nw         OXN   
3           Route 10  15e2f4643843159420d0e1b1563d7046     47nw         SAP   
29          Route 10  15e2f4643843159420d0e1b1563d7046     47nw         FIL   
595         Route 10  15e2f4643843159420d0e1b1563d7046     47nw         BFD   
75          Route 10  15e2f46438431

In [63]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt10_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 10'
                                                  )

In [64]:
chart

stop_id                        geometry                          feed_key  \
40     bLAS  POINT (434817.143 -205406.193)  d9e1e77d0754b712fc608741ae3836f5   
48     bLVT  POINT (434891.255 -205377.488)  d9e1e77d0754b712fc608741ae3836f5   
18     bBBS  POINT (274084.197 -342886.533)  d9e1e77d0754b712fc608741ae3836f5   
16     bBAR  POINT (271678.696 -341476.512)  d9e1e77d0754b712fc608741ae3836f5   
50     bMOJ  POINT (166476.324 -327734.430)  d9e1e77d0754b712fc608741ae3836f5   
76     bTEH  POINT (140979.450 -319324.182)  d9e1e77d0754b712fc608741ae3836f5   
605    bBFD   POINT (89964.411 -293278.458)  d9e1e77d0754b712fc608741ae3836f5   
30     bFIL   POINT (99427.085 -401664.847)  d9e1e77d0754b712fc608741ae3836f5   
4      bSAP   POINT (85623.126 -407336.451)  d9e1e77d0754b712fc608741ae3836f5   
54     bOXN   POINT (75916.981 -423754.747)  d9e1e77d0754b712fc608741ae3836f5   
74     bVEC   POINT (64452.501 -415204.209)  d9e1e77d0754b712fc608741ae3836f5   
14     bCPN   POINT (43838.943 -402045.428)  d9e1e77d0754b712fc608741ae3836f5   
58     bSBA   POINT (28223.118 -400226.602)  d9e1e77d0754b712fc608741ae3836f5   
6      bSBU   POINT (13946.569 -400088.258)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
40     5612              0      9:15:00        9:15:00        33300   
48     5612              1      9:35:00        9:35:00        34500   
18     5612              2     12:30:00       12:30:00        45000   
16     5612              3     12:38:00       12:38:00        45480   
50     5612              4     13:55:00       13:55:00        50100   
76     5612              5     14:23:00       14:23:00        51780   
605    5612              6     16:05:00       16:05:00        57900   
30     5612              7     17:40:00       17:40:00        63600   
4      5612              8     17:52:00       17:52:00        64320   
54     5612              9     18:22:00       18:22:00        66120   
74     5612             10     18:42:00       18:42:00        67320   
14     5612             11     19:07:00       19:07:00        68820   
58     5612             12     19:35:00       19:35:00        70500   
6      5612             13     19:55:00       19:55:00        71700   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
40           33300             9  ...             1        10   
48           34500             9  ...             1        10   
18           45000            12  ...             1        10   
16           45480            12  ...             1        10   
50           50100            13  ...             1        10   
76           51780            14  ...             1        10   
605          57900            16  ...             1        10   
30           63600            17  ...             1        10   
4            64320            17  ...             1        10   
54           66120            18  ...             1        10   
74           67320            18  ...             1        10   
14           68820            19  ...             1        10   
58           70500            19  ...             1        10   
6            71700            19  ...             1        10   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
40          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         LAS   
48          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         LVT   
18          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         BBS   
16          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         BAR   
50          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         MOJ   
76          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         TEH   
605         Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         BFD   
30          Route 10  0f3e364e0baade5ef640d8cf06f26398     j7gg         FIL   
4           Route 10  0f3e364e0baad

## Route 15a (YARTS)

* some sort of bug on 15b, 15 (both also YARTS, will check later)

In [65]:
rt15_test = sanj_long_shapes.query('route_id == "15a"')

In [66]:
rt15_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
6  Amtrak San Joaquins Schedule        Route 15a   
7  Amtrak San Joaquins Schedule        Route 15a   

                   route_long_name shape_id  
6  Merced - Yosemite National Park     8206  
7  Merced - Yosemite National Park     8ezp

In [67]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt15_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 15'
                                                  )

In [68]:
chart

stop_id                       geometry                          feed_key  \
442    bMCD  POINT (-42201.130 -78716.789)  d9e1e77d0754b712fc608741ae3836f5   
466    bMRM    POINT (2981.485 -58994.679)  d9e1e77d0754b712fc608741ae3836f5   
478    bMRP    POINT (2271.201 -58379.496)  d9e1e77d0754b712fc608741ae3836f5   
454    bMDP    POINT (7043.176 -52513.233)  d9e1e77d0754b712fc608741ae3836f5   
408    bELP   POINT (20632.432 -37538.586)  d9e1e77d0754b712fc608741ae3836f5   
490    bYOC   POINT (37788.120 -30889.448)  d9e1e77d0754b712fc608741ae3836f5   
544    bYOV   POINT (36400.210 -29748.590)  d9e1e77d0754b712fc608741ae3836f5   
419    bYOS   POINT (35254.621 -30395.837)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
442    8400              0      8:10:00        8:10:00        29400   
466    8400              1      9:00:00        9:00:00        32400   
478    8400              2      9:06:00        9:06:00        32760   
454    8400              3      9:29:00        9:29:00        34140   
408    8400              4     10:16:00       10:16:00        36960   
490    8400              5     10:46:00       10:46:00        38760   
544    8400              6     10:51:00       10:51:00        39060   
419    8400              7     10:58:00       10:58:00        39480   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
442          29400             8  ...             0       15a   
466          32400             9  ...             0       15a   
478          32760             9  ...             0       15a   
454          34140             9  ...             0       15a   
408          36960            10  ...             0       15a   
490          38760            10  ...             0       15a   
544          39060            10  ...             0       15a   
419          39480            10  ...             0       15a   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
442        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         MCD   
466        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         MRM   
478        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         MRP   
454        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         MDP   
408        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         ELP   
490        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         YOC   
544        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         YOV   
419        Route 15a  65bee65aad98f8a89aafb4917c4bda94     8206         YOS   

       stop_meters  stop_miles  next_miles  \
442       0.000000           0        37.0   
466   59148.456947          37        37.0   
478   60088.113162          37        43.0   
454   69775.096817          43        67.0   
408  107360.670861          67        81.0   
490  130245.729370          81        82.0   
544  132042.351169          82        83.0   
419  133358.141018          83         NaN   

                                            mile_range  
442  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
466                                                 []  
478               [37.0, 38.0, 39.0, 40.0, 41.0, 42.0]  
454  [43.0, 44.0, 45.0, 46.0, 47.0, 48.0, 49.0, 50....  
408  [67.0, 68.0, 69.0, 70.0, 71.0, 72.0, 73.0, 74....  
490                                             [81.0]  
544                                             [82.0]  
419                                               None  

[8 rows x 21 columns]

In [69]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt15_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 15'
                                                  )

In [70]:
chart

stop_id                       geometry                          feed_key  \
493    bYOC   POINT (37788.120 -30889.448)  d9e1e77d0754b712fc608741ae3836f5   
550    bYOV   POINT (36400.210 -29748.590)  d9e1e77d0754b712fc608741ae3836f5   
422    bYOS   POINT (35254.621 -30395.837)  d9e1e77d0754b712fc608741ae3836f5   
411    bELP   POINT (20632.432 -37538.586)  d9e1e77d0754b712fc608741ae3836f5   
457    bMDP    POINT (7043.176 -52513.233)  d9e1e77d0754b712fc608741ae3836f5   
481    bMRP    POINT (2271.201 -58379.496)  d9e1e77d0754b712fc608741ae3836f5   
469    bMRM    POINT (2981.485 -58994.679)  d9e1e77d0754b712fc608741ae3836f5   
445    bMCD  POINT (-42201.130 -78716.789)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
493    8415              0     12:00:00       12:00:00        43200   
550    8415              1     12:14:00       12:14:00        44040   
422    8415              2     12:19:00       12:19:00        44340   
411    8415              3     12:47:00       12:47:00        46020   
457    8415              4     13:29:00       13:29:00        48540   
481    8415              5     13:55:00       13:55:00        50100   
469    8415              6     13:58:00       13:58:00        50280   
445    8415              7     14:57:00       14:57:00        53820   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
493          43200            12  ...             1       15a   
550          44040            12  ...             1       15a   
422          44340            12  ...             1       15a   
411          46020            12  ...             1       15a   
457          48540            13  ...             1       15a   
481          50100            13  ...             1       15a   
469          50280            13  ...             1       15a   
445          53820            14  ...             1       15a   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
493        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         YOC   
550        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         YOV   
422        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         YOS   
411        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         ELP   
457        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         MDP   
481        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         MRP   
469        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         MRM   
445        Route 15a  a6803bd09ae68d870f1f0d263d100fe1     8ezp         MCD   

       stop_meters  stop_miles  next_miles  \
493       0.000000           0         2.0   
550    2426.603361           2         2.0   
422    3992.149061           2        15.0   
411   24109.240549          15        38.0   
457   61702.721446          38        45.0   
481   72226.819843          45        46.0   
469   73614.207167          46        83.0   
445  133980.921771          83         NaN   

                                            mile_range  
493                                         [0.0, 1.0]  
550                                                 []  
422  [2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0,...  
411  [15.0, 16.0, 17.0, 18.0, 19.0, 20.0, 21.0, 22....  
457         [38.0, 39.0, 40.0, 41.0, 42.0, 43.0, 44.0]  
481                                             [45.0]  
469  [46.0, 47.0, 48.0, 49.0, 50.0, 51.0, 52.0, 53....  
445                                               None  

[8 rows x 21 columns]

## Route 18

In [71]:
rt18_test = sanj_long_shapes.query('route_id == "18"')

In [72]:
rt18_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
10  Amtrak San Joaquins Schedule         Route 18   
11  Amtrak San Joaquins Schedule         Route 18   

                             route_long_name shape_id  
10  Santa Maria - San Luis Obispo - Handford     pr9d  
11  Santa Maria - San Luis Obispo - Handford     vaq5

In [73]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt18_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 18'
                                                  )

In [74]:
chart

stop_id                        geometry                          feed_key  \
55    bSAT  POINT (-37992.525 -340528.248)  d9e1e77d0754b712fc608741ae3836f5   
37    bGVB  POINT (-57245.933 -321451.522)  d9e1e77d0754b712fc608741ae3836f5   
9     bSLO  POINT (-59491.603 -304273.178)  d9e1e77d0754b712fc608741ae3836f5   
65    bSLP  POINT (-59764.526 -301635.977)  d9e1e77d0754b712fc608741ae3836f5   
27    bATA  POINT (-60253.317 -280672.242)  d9e1e77d0754b712fc608741ae3836f5   
69    bPRB  POINT (-62243.055 -265807.946)  d9e1e77d0754b712fc608741ae3836f5   
43    bLMC    POINT (8017.063 -195088.455)  d9e1e77d0754b712fc608741ae3836f5   
79    bHNF   POINT (31204.915 -187822.172)  d9e1e77d0754b712fc608741ae3836f5   
77    bVIS   POINT (63787.809 -187018.565)  d9e1e77d0754b712fc608741ae3836f5   

   trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
55    4015              0      8:45:00        8:45:00        31500   
37    4015              1      9:05:00        9:05:00        32700   
9     4015              2      9:35:00        9:35:00        34500   
65    4015              3      9:45:00        9:45:00        35100   
27    4015              4     10:05:00       10:05:00        36300   
69    4015              5     10:30:00       10:30:00        37800   
43    4015              6     12:00:00       12:00:00        43200   
79    4015              7     12:10:00       12:10:00        43800   
77    4015              8     12:30:00       12:30:00        45000   

    departure_sec  arrival_hour  ...  direction_id  route_id route_short_name  \
55          31500             8  ...             0        18         Route 18   
37          32700             9  ...             0        18         Route 18   
9           34500             9  ...             0        18         Route 18   
65          35100             9  ...             0        18         Route 18   
27          36300            10  ...             0        18         Route 18   
69          37800            10  ...             0        18         Route 18   
43          43200            12  ...             0        18         Route 18   
79          43800            12  ...             0        18         Route 18   
77          45000            12  ...             0        18         Route 18   

                     shape_array_key shape_id amtrak_stop    stop_meters  \
55  13bf0c42da40504905df1cb382bf86fe     pr9d         SAT       0.000000   
37  13bf0c42da40504905df1cb382bf86fe     pr9d         GVB   31036.576224   
9   13bf0c42da40504905df1cb382bf86fe     pr9d         SLO   51318.896546   
65  13bf0c42da40504905df1cb382bf86fe     pr9d         SLP   55001.825628   
27  13bf0c42da40504905df1cb382bf86fe     pr9d         ATA   82199.656483   
69  13bf0c42da40504905df1cb382bf86fe     pr9d         PRB  100339.520955   
43  13bf0c42da40504905df1cb382bf86fe     pr9d         LMC  232286.615923   
79  13bf0c42da40504905df1cb382bf86fe     pr9d         HNF  258258.588494   
77  13bf0c42da40504905df1cb382bf86fe     pr9d         VIS  292300.791293   

    stop_miles  next_miles                                         mile_range  
55           0        19.0  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
37          19        32.0  [19.0, 20.0, 21.0, 22.0, 23.0, 24.0, 25.0, 26....  
9           32        34.0                                       [32.0, 33.0]  
65          34        51.0  [34.0, 35.0, 36.0, 37.0, 38.0, 39.0, 40.0, 41....  
27          51        62.0  [51.0, 52.0, 53.0, 54.0, 55.0, 56.0, 57.0, 58....  
69          62       144.0  [62.0, 63.0, 64.0, 65.0, 66.0, 67.0, 68.0, 69....  
43         144       160.0  [144.0, 145.0, 146.0, 147.0, 148.0, 149.0, 150...  
79         160       182.0  [160.0, 161.0, 162.0, 163.0, 164.0, 165.0, 166...  
77         182         NaN                                               None  

[9 rows x 21 columns]

In [75]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt18_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 18'
                                                  )

In [76]:
chart

stop_id                        geometry                          feed_key  \
78    bVIS   POINT (63787.809 -187018.565)  d9e1e77d0754b712fc608741ae3836f5   
81    bHNF   POINT (31204.915 -187822.172)  d9e1e77d0754b712fc608741ae3836f5   
44    bLMC    POINT (8017.063 -195088.455)  d9e1e77d0754b712fc608741ae3836f5   
70    bPRB  POINT (-62243.055 -265807.946)  d9e1e77d0754b712fc608741ae3836f5   
28    bATA  POINT (-60253.317 -280672.242)  d9e1e77d0754b712fc608741ae3836f5   
66    bSLP  POINT (-59764.526 -301635.977)  d9e1e77d0754b712fc608741ae3836f5   
10    bSLO  POINT (-59491.603 -304273.178)  d9e1e77d0754b712fc608741ae3836f5   
38    bGVB  POINT (-57245.933 -321451.522)  d9e1e77d0754b712fc608741ae3836f5   
56    bSAT  POINT (-37992.525 -340528.248)  d9e1e77d0754b712fc608741ae3836f5   

   trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
78    4010              0     13:00:00       13:00:00        46800   
81    4010              1     13:50:00       13:50:00        49800   
44    4010              2     14:05:00       14:05:00        50700   
70    4010              3     15:35:00       15:35:00        56100   
28    4010              4     15:50:00       15:50:00        57000   
66    4010              5     16:05:00       16:05:00        57900   
10    4010              6     16:15:00       16:15:00        58500   
38    4010              7     16:40:00       16:40:00        60000   
56    4010              8     17:05:00       17:05:00        61500   

    departure_sec  arrival_hour  ...  direction_id  route_id route_short_name  \
78          46800            13  ...             1        18         Route 18   
81          49800            13  ...             1        18         Route 18   
44          50700            14  ...             1        18         Route 18   
70          56100            15  ...             1        18         Route 18   
28          57000            15  ...             1        18         Route 18   
66          57900            16  ...             1        18         Route 18   
10          58500            16  ...             1        18         Route 18   
38          60000            16  ...             1        18         Route 18   
56          61500            17  ...             1        18         Route 18   

                     shape_array_key shape_id amtrak_stop    stop_meters  \
78  b172867a38084306ce280db490b246ae     vaq5         VIS       0.000000   
81  b172867a38084306ce280db490b246ae     vaq5         HNF   33650.119667   
44  b172867a38084306ce280db490b246ae     vaq5         LMC   59547.385127   
70  b172867a38084306ce280db490b246ae     vaq5         PRB  191412.894328   
28  b172867a38084306ce280db490b246ae     vaq5         ATA  209614.654692   
66  b172867a38084306ce280db490b246ae     vaq5         SLP  236528.180790   
10  b172867a38084306ce280db490b246ae     vaq5         SLO  240658.618982   
38  b172867a38084306ce280db490b246ae     vaq5         GVB  261127.756248   
56  b172867a38084306ce280db490b246ae     vaq5         SAT  292275.378816   

    stop_miles  next_miles                                         mile_range  
78           0        21.0  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
81          21        37.0  [21.0, 22.0, 23.0, 24.0, 25.0, 26.0, 27.0, 28....  
44          37       119.0  [37.0, 38.0, 39.0, 40.0, 41.0, 42.0, 43.0, 44....  
70         119       130.0  [119.0, 120.0, 121.0, 122.0, 123.0, 124.0, 125...  
28         130       147.0  [130.0, 131.0, 132.0, 133.0, 134.0, 135.0, 136...  
66         147       150.0                              [147.0, 148.0, 149.0]  
10         150       162.0  [150.0, 151.0, 152.0, 153.0, 154.0, 155.0, 156...  
38         162       182.0  [162.0, 163.0, 164.0, 165.0, 166.0, 167.0, 168...  
56         182         NaN                                               None  

[9 rows x 21 columns]

## Route 19

In [77]:
rt19_test = sanj_long_shapes.query('route_id == "19"')

In [78]:
rt19_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
12  Amtrak San Joaquins Schedule         Route 19   
13  Amtrak San Joaquins Schedule         Route 19   

                 route_long_name shape_id  
12  Berkersfield - Inland Empire     6v3p  
13  Berkersfield - Inland Empire     h413

In [79]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt19_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 19')

In [80]:
chart

stop_id                        geometry                          feed_key  \
613    bBFD   POINT (89964.411 -293278.458)  d9e1e77d0754b712fc608741ae3836f5   
116    bLCA  POINT (159660.238 -418969.923)  d9e1e77d0754b712fc608741ae3836f5   
152    bPAS  POINT (171397.986 -428615.413)  d9e1e77d0754b712fc608741ae3836f5   
88     bCLM  POINT (210662.754 -433175.903)  d9e1e77d0754b712fc608741ae3836f5   
136    bONA  POINT (216893.930 -436642.192)  d9e1e77d0754b712fc608741ae3836f5   
160    bRIV  POINT (243023.880 -445473.844)  d9e1e77d0754b712fc608741ae3836f5   
164    bSNB  POINT (247949.209 -431101.216)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
613    5412              0     16:05:00       16:05:00        57900   
116    5412              1     17:55:00       17:55:00        64500   
152    5412              2     18:10:00       18:10:00        65400   
88     5412              3     19:00:00       19:00:00        68400   
136    5412              4     19:17:00       19:17:00        69420   
160    5412              5     19:40:00       19:40:00        70800   
164    5412              6     20:00:00       20:00:00        72000   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
613          57900            16  ...             0        19   
116          64500            17  ...             0        19   
152          65400            18  ...             0        19   
88           68400            19  ...             0        19   
136          69420            19  ...             0        19   
160          70800            19  ...             0        19   
164          72000            20  ...             0        19   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
613         Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         BFD   
116         Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         LCA   
152         Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         PAS   
88          Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         CLM   
136         Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         ONA   
160         Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         RIV   
164         Route 19  b6cc209a98a4bca5c7e6e99473475b2a     6v3p         SNB   

       stop_meters  stop_miles  next_miles  \
613       0.000000           0       104.0   
116  167639.180611         104       115.0   
152  185013.877534         115       143.0   
88   229358.004612         143       149.0   
136  240572.179743         149       171.0   
160  275213.939206         171       182.0   
164  293152.304650         182         NaN   

                                            mile_range  
613  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
116  [104.0, 105.0, 106.0, 107.0, 108.0, 109.0, 110...  
152  [115.0, 116.0, 117.0, 118.0, 119.0, 120.0, 121...  
88          [143.0, 144.0, 145.0, 146.0, 147.0, 148.0]  
136  [149.0, 150.0, 151.0, 152.0, 153.0, 154.0, 155...  
160  [171.0, 172.0, 173.0, 174.0, 175.0, 176.0, 177...  
164                                               None  

[7 rows x 21 columns]

In [81]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt19_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 19')

In [82]:
chart

stop_id                        geometry                          feed_key  \
162    bSNB  POINT (247949.209 -431101.216)  d9e1e77d0754b712fc608741ae3836f5   
158    bRIV  POINT (243023.880 -445473.844)  d9e1e77d0754b712fc608741ae3836f5   
134    bONA  POINT (216893.930 -436642.192)  d9e1e77d0754b712fc608741ae3836f5   
86     bCLM  POINT (210662.754 -433175.903)  d9e1e77d0754b712fc608741ae3836f5   
150    bPAS  POINT (171397.986 -428615.413)  d9e1e77d0754b712fc608741ae3836f5   
114    bLCA  POINT (159660.238 -418969.923)  d9e1e77d0754b712fc608741ae3836f5   
600    bBFD   POINT (89964.411 -293278.458)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
162    5415              0      7:30:00        7:30:00        27000   
158    5415              1      7:50:00        7:50:00        28200   
134    5415              2      8:15:00        8:15:00        29700   
86     5415              3      8:40:00        8:40:00        31200   
150    5415              4      9:20:00        9:20:00        33600   
114    5415              5      9:45:00        9:45:00        35100   
600    5415              6     11:55:00       11:55:00        42900   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
162          27000             7  ...             1        19   
158          28200             7  ...             1        19   
134          29700             8  ...             1        19   
86           31200             8  ...             1        19   
150          33600             9  ...             1        19   
114          35100             9  ...             1        19   
600          42900            11  ...             1        19   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
162         Route 19  f1d856403457769a162d25db64a93170     h413         SNB   
158         Route 19  f1d856403457769a162d25db64a93170     h413         RIV   
134         Route 19  f1d856403457769a162d25db64a93170     h413         ONA   
86          Route 19  f1d856403457769a162d25db64a93170     h413         CLM   
150         Route 19  f1d856403457769a162d25db64a93170     h413         PAS   
114         Route 19  f1d856403457769a162d25db64a93170     h413         LCA   
600         Route 19  f1d856403457769a162d25db64a93170     h413         BFD   

       stop_meters  stop_miles  next_miles  \
162       0.000000           0        11.0   
158   18116.175107          11        33.0   
134   52598.374860          33        40.0   
86    64124.087097          40        67.0   
150  108624.318264          67        78.0   
114  125670.675251          78       181.0   
600  291198.974631         181         NaN   

                                            mile_range  
162  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
158  [11.0, 12.0, 13.0, 14.0, 15.0, 16.0, 17.0, 18....  
134         [33.0, 34.0, 35.0, 36.0, 37.0, 38.0, 39.0]  
86   [40.0, 41.0, 42.0, 43.0, 44.0, 45.0, 46.0, 47....  
150  [67.0, 68.0, 69.0, 70.0, 71.0, 72.0, 73.0, 74....  
114  [78.0, 79.0, 80.0, 81.0, 82.0, 83.0, 84.0, 85....  
600                                               None  

[7 rows x 21 columns]

## Route 20

In [83]:
rt20_test = sanj_long_shapes.query('route_id == "20"')

In [84]:
rt20_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
16  Amtrak San Joaquins Schedule         Route 20   
17  Amtrak San Joaquins Schedule         Route 20   

                                   route_long_name shape_id  
16  Sparks-Reno- Roseville- Lake Tahoe- Sacramento     aa9c  
17  Sparks-Reno- Roseville- Lake Tahoe- Sacramento     0pcy

In [85]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt20_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 20')

In [86]:
chart

stop_id                       geometry                          feed_key  \
355    bRSV  POINT (-111662.733 82313.272)  d9e1e77d0754b712fc608741ae3836f5   
587    bSAC  POINT (-130615.865 63942.803)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
355    3623              0      4:15:00        4:15:00        15300   
587    3623              1      4:55:00        4:55:00        17700   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
355          15300             4  ...             0        20   
587          17700             4  ...             0        20   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
355         Route 20  3f89f749662c072021ab5ff642e92e05     aa9c         RSV   
587         Route 20  3f89f749662c072021ab5ff642e92e05     aa9c         SAC   

       stop_meters  stop_miles  next_miles  \
355  198541.109402         123       143.0   
587  229532.225678         143         NaN   

                                            mile_range  
355  [123.0, 124.0, 125.0, 126.0, 127.0, 128.0, 129...  
587                                               None  

[2 rows x 21 columns]

In [87]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt20_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 20')

In [88]:
chart

stop_id                       geometry                          feed_key  \
578    bSAC  POINT (-130615.865 63942.803)  d9e1e77d0754b712fc608741ae3836f5   
351    bRSV  POINT (-111662.733 82313.272)  d9e1e77d0754b712fc608741ae3836f5   
306    bRLN  POINT (-107355.643 86810.624)  d9e1e77d0754b712fc608741ae3836f5   
278    bARN   POINT (-93818.050 99094.198)  d9e1e77d0754b712fc608741ae3836f5   
24     bCOX  POINT (-82357.550 120740.984)  d9e1e77d0754b712fc608741ae3836f5   
188    bTRU  POINT (-15998.708 145764.270)  d9e1e77d0754b712fc608741ae3836f5   
168    bRNO   POINT (16204.137 168114.986)  d9e1e77d0754b712fc608741ae3836f5   
72     bSPX   POINT (20905.716 168773.966)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
578   3713W              0     14:25:00       14:25:00        51900   
351   3713W              1     14:55:00       14:55:00        53700   
306   3713W              2     15:10:00       15:10:00        54600   
278   3713W              3     15:35:00       15:35:00        56100   
24    3713W              4     15:50:00       15:50:00        57000   
188   3713W              5     17:10:00       17:10:00        61800   
168   3713W              6     17:50:00       17:50:00        64200   
72    3713W              7     18:10:00       18:10:00        65400   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
578          51900            14  ...             1        20   
351          53700            14  ...             1        20   
306          54600            15  ...             1        20   
278          56100            15  ...             1        20   
24           57000            15  ...             1        20   
188          61800            17  ...             1        20   
168          64200            17  ...             1        20   
72           65400            18  ...             1        20   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
578         Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         SAC   
351         Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         RSV   
306         Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         RLN   
278         Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         ARN   
24          Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         COX   
188         Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         TRU   
168         Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         RNO   
72          Route 20  cb3177f17d1d4e3359f07c2af34a6ad5     0pcy         SPX   

       stop_meters  stop_miles  next_miles  \
578       0.000000           0        20.0   
351   31897.659258          20        25.0   
306   39632.180351          25        38.0   
278   60730.751890          38        54.0   
24    87387.649726          54       106.0   
188  170963.403855         106       139.0   
168  222991.613501         139       142.0   
72   229132.123608         142         NaN   

                                            mile_range  
578  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
351                     [20.0, 21.0, 22.0, 23.0, 24.0]  
306  [25.0, 26.0, 27.0, 28.0, 29.0, 30.0, 31.0, 32....  
278  [38.0, 39.0, 40.0, 41.0, 42.0, 43.0, 44.0, 45....  
24   [54.0, 55.0, 56.0, 57.0, 58.0, 59.0, 60.0, 61....  
188  [106.0, 107.0, 108.0, 109.0, 110.0, 111.0, 112...  
168                              [139.0, 140.0, 141.0]  
72                                                None  

[8 rows x 21 columns]

## Route 20c

In [89]:
rt20c_test = sanj_long_shapes.query('route_id == "20c"')

In [90]:
rt20c_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
18  Amtrak San Joaquins Schedule        Route 20c   
19  Amtrak San Joaquins Schedule        Route 20c   

                  route_long_name shape_id  
18  Sacramento - South Lake Tahoe     t7hi  
19  Sacramento - South Lake Tahoe     ub54

In [91]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt20c_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 20'
                                                  )

In [92]:
chart

stop_id                       geometry                          feed_key  \
564    bSAC  POINT (-130615.865 63942.803)  d9e1e77d0754b712fc608741ae3836f5   
25     bCPC   POINT (-86804.342 71764.388)  d9e1e77d0754b712fc608741ae3836f5   
61     bPCV   POINT (-68556.414 79949.546)  d9e1e77d0754b712fc608741ae3836f5   
7      bSLT     POINT (-431.664 99679.795)  d9e1e77d0754b712fc608741ae3836f5   
63     bSLH    POINT (5017.717 104646.270)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
564    3624              0     10:00:00       10:00:00        36000   
25     3624              1     10:40:00       10:40:00        38400   
61     3624              2     11:00:00       11:00:00        39600   
7      3624              3     12:20:00       12:20:00        44400   
63     3624              4     12:30:00       12:30:00        45000   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
564          36000            10  ...             0       20c   
25           38400            10  ...             0       20c   
61           39600            11  ...             0       20c   
7            44400            12  ...             0       20c   
63           45000            12  ...             0       20c   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
564        Route 20c  8e658598f9c47bb53359da75b774698f     t7hi         SAC   
25         Route 20c  8e658598f9c47bb53359da75b774698f     t7hi         CPC   
61         Route 20c  8e658598f9c47bb53359da75b774698f     t7hi         PCV   
7          Route 20c  8e658598f9c47bb53359da75b774698f     t7hi         SLT   
63         Route 20c  8e658598f9c47bb53359da75b774698f     t7hi         SLH   

       stop_meters  stop_miles  next_miles  \
564       0.000000           0        32.0   
25    51740.896130          32        46.0   
61    73989.575104          46       103.0   
7    165022.183224         103       107.0   
63   172395.217427         107         NaN   

                                            mile_range  
564  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, ...  
25   [32.0, 33.0, 34.0, 35.0, 36.0, 37.0, 38.0, 39....  
61   [46.0, 47.0, 48.0, 49.0, 50.0, 51.0, 52.0, 53....  
7                         [103.0, 104.0, 105.0, 106.0]  
63                                                None  

[5 rows x 21 columns]

In [93]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt20c_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 20'
                                                  )

In [94]:
chart

stop_id                       geometry                          feed_key  \
64     bSLH    POINT (5017.717 104646.270)  d9e1e77d0754b712fc608741ae3836f5   
8      bSLT     POINT (-431.664 99679.795)  d9e1e77d0754b712fc608741ae3836f5   
62     bPCV   POINT (-68556.414 79949.546)  d9e1e77d0754b712fc608741ae3836f5   
26     bCPC   POINT (-86804.342 71764.388)  d9e1e77d0754b712fc608741ae3836f5   
576    bSAC  POINT (-130615.865 63942.803)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
64     3647              0     13:25:00       13:25:00        48300   
8      3647              1     13:40:00       13:40:00        49200   
62     3647              2     15:00:00       15:00:00        54000   
26     3647              3     15:15:00       15:15:00        54900   
576    3647              4     16:45:00       16:45:00        60300   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
64           48300            13  ...             1       20c   
8            49200            13  ...             1       20c   
62           54000            15  ...             1       20c   
26           54900            15  ...             1       20c   
576          60300            16  ...             1       20c   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
64         Route 20c  35809685c779990d8a7b271434e630bb     ub54         SLH   
8          Route 20c  35809685c779990d8a7b271434e630bb     ub54         SLT   
62         Route 20c  35809685c779990d8a7b271434e630bb     ub54         PCV   
26         Route 20c  35809685c779990d8a7b271434e630bb     ub54         CPC   
576        Route 20c  35809685c779990d8a7b271434e630bb     ub54         SAC   

       stop_meters  stop_miles  next_miles  \
64        0.000000           0         5.0   
8      8106.511375           5        61.0   
62    98915.838888          61        75.0   
26   120611.889257          75       106.0   
576  171244.470142         106         NaN   

                                            mile_range  
64                           [0.0, 1.0, 2.0, 3.0, 4.0]  
8    [5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 11.0, 12.0, 13...  
62   [61.0, 62.0, 63.0, 64.0, 65.0, 66.0, 67.0, 68....  
26   [75.0, 76.0, 77.0, 78.0, 79.0, 80.0, 81.0, 82....  
576                                               None  

[5 rows x 21 columns]

## Route 99

In [95]:
rt99_test = sanj_long_shapes.query('route_id == "99"')

In [96]:
rt99_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
26  Amtrak San Joaquins Schedule         Route 99   
27  Amtrak San Joaquins Schedule         Route 99   

                     route_long_name shape_id  
26  Oakland-Emeryville-San Francisco     p5wu  
27  Oakland-Emeryville-San Francisco     f1x5

In [97]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt99_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 99')

In [98]:
chart

stop_id                        geometry                          feed_key  \
379    bSFC  POINT (-210915.953 -22663.029)  d9e1e77d0754b712fc608741ae3836f5   
369    bEMY  POINT (-201396.113 -17122.117)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
379    6616              0     12:50:00       12:50:00        46200   
369    6616              1     13:20:00       13:20:00        48000   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
379          46200            12  ...             0        99   
369          48000            13  ...             0        99   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
379         Route 99  82db3c1be8f398c6f49d9db438eaa443     p5wu         SFC   
369         Route 99  82db3c1be8f398c6f49d9db438eaa443     p5wu         EMY   

      stop_meters  stop_miles  next_miles  \
379      0.000000           0         8.0   
369  13267.401956           8         NaN   

                                   mile_range  
379  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0]  
369                                      None  

[2 rows x 21 columns]

In [99]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt99_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 99')

In [100]:
chart

stop_id                        geometry                          feed_key  \
373    bEMY  POINT (-201396.113 -17122.117)  d9e1e77d0754b712fc608741ae3836f5   
383    bSFC  POINT (-210915.953 -22663.029)  d9e1e77d0754b712fc608741ae3836f5   

    trip_id  stop_sequence arrival_time departure_time  arrival_sec  \
373    6617              0     20:20:00       20:20:00        73200   
383    6617              1     20:50:00       20:50:00        75000   

     departure_sec  arrival_hour  ...  direction_id  route_id  \
373          73200            20  ...             1        99   
383          75000            20  ...             1        99   

    route_short_name                   shape_array_key shape_id amtrak_stop  \
373         Route 99  ef9cbdb19e2f885fb77ba9da12ed3d3e     f1x5         EMY   
383         Route 99  ef9cbdb19e2f885fb77ba9da12ed3d3e     f1x5         SFC   

      stop_meters  stop_miles  next_miles  \
373      0.000000           0         9.0   
383  14387.977015           9         NaN   

                                        mile_range  
373  [0.0, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0]  
383                                           None  

[2 rows x 21 columns]

## Route 1 (time test)

In [156]:
rt1_test = sanj_long_shapes.query('route_id == "1"')

In [157]:
rt1_test[['name', 'route_short_name', 'route_long_name', 'shape_id']]

name route_short_name  \
0  Amtrak San Joaquins Schedule          Route 1   
1  Amtrak San Joaquins Schedule          Route 1   

                                     route_long_name shape_id  
0  Fresno/Bekersfield - Los Angeles- SantaAna - O...     jfy7  
1  Fresno/Bekersfield - Los Angeles- SantaAna - O...     xurp

In [163]:
importlib.reload(chart_utils)

<module 'chart_utils' from '/home/jovyan/data-analyses/thruway_intercity_bus/chart_utils.py'>

In [164]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A')

In [165]:
chart

alt.Chart(...)

In [166]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[0], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A', how='time')

In [167]:
chart

alt.Chart(...)

In [168]:
chart = chart_utils.flow_chart_from_shape_trip_row(rt1_test.iloc[1], stop_times=bus_st, ridership=source_ridership,
                              ridership_data_route='Rt 1A', how='time')

In [169]:
chart

alt.Chart(...)